# Initial data processing

## Cleaning the data

We are using human-generated neural reconstructions as our ground truth. The first step is to get rid of comments in the header of the file

In [51]:
import os

def get_human_trajectories():
    file_list = glob.glob("../data/human/*.swc")
    return file_list

def remove_comments(fpaths, fnames):
    """SWC files start with comments, remove before proceeding"""
    for i in range(len(fpaths)):

        input = open(fpaths[i], "r")
        outdir = "../data/human_clean/"
        outdir = os.path.abspath(outdir)
        if not os.path.exists(outdir):
            os.mkdir(outdir)
        outfile = os.path.join(outdir, fnames[i])
        output = open(outfile, "w+")

        for line in input:
            if not line.lstrip().startswith("#"):
                output.write(line)

        input.close()
        output.close()

def main():
    # get human trajectories
    fnames = []
    abs_paths = []
    for root, dirs, fnames_ in os.walk("../data/human/"):
        fnames.extend(fnames_)
        for f in fnames_:
            relpath = os.path.join(root, f)
            abs_path = os.path.abspath(relpath)
            abs_paths.append(abs_path)

    remove_comments(abs_paths, fnames)


main()

## Parsing SWC files

Next, we need to split each file into its component branches. The SWC files have the following columns:

`node_id type x_coordinate y_coordinate z_coordinate radius parent_node`

First, I convert the SWC file into a linked list.

In [52]:
from collections import defaultdict

def file_to_linked_list(fpath: list):
    
    # https://stackoverflow.com/a/17756005/4212158
    linked_list = defaultdict(list)
    
    input = open(fpath, "r")
    for line in input:
        # note: if the parent node is -1, then the child_node_id is the true identity of the root node
        child_node_id, type_, x_coord, y_coord, z_coord, radius, parent_node = line.split()
        new_node = (child_node_id, x_coord, y_coord, z_coord)
        if len(new_node) != 4:
            raise Exception("faulty node: {}".format(new_node))
        linked_list[parent_node].append(new_node)
    
    input.close()
    return linked_list


## Chopping  reconstructions into individual branches

I start tracing the neuron starting at each root node, which by convention has a parent_node_id of -1. From each root node, I start to grow the branch

In [53]:
def chop_graph(fname: str, linked_list: dict):
    """take a single reconstruction, and chop it up at every fork"""
    assert isinstance(linked_list, dict)
    
    root_nodes = linked_list["-1"]
    for i, root_node in enumerate(root_nodes):
        print("scanning {} root node {} of {}".format(fname, i, len(root_nodes)))
        root_node_id, _x_coord, _y_coord, _z_coord = root_node

        child_nodes = linked_list[root_node_id]
        for j, child_node in enumerate(child_nodes):
            print("starting child {} of {}".format(j, len(child_nodes)))
            child_node_id,  _x_coord, _y_coord, _z_coord = child_node
            branch_name = "_".join([fname, "root{}".format(root_node_id), "child{}".format(child_node_id)])
            grow_branch(linked_list, root_node_id, child_node_id, branch_name)
            
            

I grow each branch until I encounter a fork. Forks are easy to find because the parent node will have more than one child. When the 

In [54]:
def grow_branch(linked_list: dict, root_node_id: str, first_child_node_id: str, branch_name: str):
    """grow the branch until there's a fork"""
    assert isinstance(linked_list, dict)
    
    # initialize the branch
    print("new branch started: {}".format(branch_name))
    branch = [root_node_id, first_child_node_id]
    
    end_found = False
    parent_node_id = first_child_node_id
    while not end_found:
        if (len(branch) % 10000000 == 0):
            print("{} nodes processed".format(len(branch)))
        try:
            child_nodes = linked_list[parent_node_id]
            if len(child_nodes) > 1: # fork found
                print("fork found after {} nodes".format(len(branch)))
                save_branch_as_swc(branch, branch_name)
                for i, child_node in enumerate(child_nodes):
                    child_node_id, _x_coord, _y_coord, _z_coord = child_node
                    child_branch_name = "_".join(branch_name, "grandchild{}".format(child_node_id))
                    grow_branch(linked_list, parent_node_id, child_node)
                end_found = True
            else:
                branch.append(child_nodes)  # should be just 1 node
                parent_node = child_nodes
        except KeyError:  # no more children
            print("end of branch {} found after {} nodes".format(branch_name, len(branch)))
            save_branch_as_swc(branch, branch_name)
            end_found = True

Finally, save each branch as its own SWC file. Reminder, the column order convention is 

`node_id type x_coordinate y_coordinate z_coordinate radius parent_node`

In [ ]:
def save_branch_as_swc(branch, branch_name):   
    outdir = "../data/human_splitted/"
    outdir = os.path.abspath(outdir)
    if not os.path.exists(outdir):
        os.mkdir(outdir)
    outfile = os.path.join(outdir, branch_name, ".swc")
    print("saving SWC {}".format(branch_name))
    output = open(outfile, "w+")
    
    default_radius = 1.0
    default_type = 3
    
    parent_node_id = "-1"
    for i, node in enumerate(branch):
        child_node_id, x, y, z = node
        swc_line = " ".join(child_node_id, default_type, x, y, z, default_radius, parent_node_id)
        output.write(swc_line)
        parent_node_id = child_node_id

    output.close()

Now, we can go through the list of clean files and actually split everything.

In [ ]:
clean_files = []
fnames = []
for root, dirs, fnames_ in os.walk("../data/human_clean/"):
        fnames.extend(fnames_)
        for f in fnames_:
            relpath = os.path.join(root, f)
            abs_path = os.path.abspath(relpath)
            clean_files.append(abs_path)
assert len(clean_files) == len(fnames), "# file paths and fnames don't match: {} and {}".format(len(clean_files), len(fnames))

#linked_lists = []
for i in range(len(fnames)):
    print("#{} parsing {} to linked list".format(i, fnames[i]))
    if i < 1: # TODO remove after debugging
        linked_list = file_to_linked_list(clean_files[i])
        print("#{} splitting {} to branches".format(i, fnames[i]))
        chop_graph(fnames[i], linked_list)

#0 parsing 110_ZWX_LijLiu_06072018.ano.swc to linked list
#0 splitting 110_ZWX_LijLiu_06072018.ano.swc to branches
scanning 110_ZWX_LijLiu_06072018.ano.swc root node 0 of 929
starting child 0 of 1
new branch started: 110_ZWX_LijLiu_06072018.ano.swc_root5497882_child5497881
500 nodes processed
1000 nodes processed
1500 nodes processed
2000 nodes processed
2500 nodes processed
3000 nodes processed
3500 nodes processed
4000 nodes processed
4500 nodes processed
5000 nodes processed
5500 nodes processed
6000 nodes processed
6500 nodes processed
7000 nodes processed
7500 nodes processed
8000 nodes processed
8500 nodes processed
9000 nodes processed
9500 nodes processed
10000 nodes processed
10500 nodes processed
11000 nodes processed
11500 nodes processed
12000 nodes processed
12500 nodes processed
13000 nodes processed
13500 nodes processed
14000 nodes processed
14500 nodes processed
15000 nodes processed
15500 nodes processed
16000 nodes processed
16500 nodes processed
17000 nodes processe

411500 nodes processed
412000 nodes processed
412500 nodes processed
413000 nodes processed
413500 nodes processed
414000 nodes processed
414500 nodes processed
415000 nodes processed
415500 nodes processed
416000 nodes processed
416500 nodes processed
417000 nodes processed
417500 nodes processed
418000 nodes processed
418500 nodes processed
419000 nodes processed
419500 nodes processed
420000 nodes processed
420500 nodes processed
421000 nodes processed
421500 nodes processed
422000 nodes processed
422500 nodes processed
423000 nodes processed
423500 nodes processed
424000 nodes processed
424500 nodes processed
425000 nodes processed
425500 nodes processed
426000 nodes processed
426500 nodes processed
427000 nodes processed
427500 nodes processed
428000 nodes processed
428500 nodes processed
429000 nodes processed
429500 nodes processed
430000 nodes processed
430500 nodes processed
431000 nodes processed
431500 nodes processed
432000 nodes processed
432500 nodes processed
433000 node

865000 nodes processed
865500 nodes processed
866000 nodes processed
866500 nodes processed
867000 nodes processed
867500 nodes processed
868000 nodes processed
868500 nodes processed
869000 nodes processed
869500 nodes processed
870000 nodes processed
870500 nodes processed
871000 nodes processed
871500 nodes processed
872000 nodes processed
872500 nodes processed
873000 nodes processed
873500 nodes processed
874000 nodes processed
874500 nodes processed
875000 nodes processed
875500 nodes processed
876000 nodes processed
876500 nodes processed
877000 nodes processed
877500 nodes processed
878000 nodes processed
878500 nodes processed
879000 nodes processed
879500 nodes processed
880000 nodes processed
880500 nodes processed
881000 nodes processed
881500 nodes processed
882000 nodes processed
882500 nodes processed
883000 nodes processed
883500 nodes processed
884000 nodes processed
884500 nodes processed
885000 nodes processed
885500 nodes processed
886000 nodes processed
886500 node

1228000 nodes processed
1228500 nodes processed
1229000 nodes processed
1229500 nodes processed
1230000 nodes processed
1230500 nodes processed
1231000 nodes processed
1231500 nodes processed
1232000 nodes processed
1232500 nodes processed
1233000 nodes processed
1233500 nodes processed
1234000 nodes processed
1234500 nodes processed
1235000 nodes processed
1235500 nodes processed
1236000 nodes processed
1236500 nodes processed
1237000 nodes processed
1237500 nodes processed
1238000 nodes processed
1238500 nodes processed
1239000 nodes processed
1239500 nodes processed
1240000 nodes processed
1240500 nodes processed
1241000 nodes processed
1241500 nodes processed
1242000 nodes processed
1242500 nodes processed
1243000 nodes processed
1243500 nodes processed
1244000 nodes processed
1244500 nodes processed
1245000 nodes processed
1245500 nodes processed
1246000 nodes processed
1246500 nodes processed
1247000 nodes processed
1247500 nodes processed
1248000 nodes processed
1248500 nodes pr

1661000 nodes processed
1661500 nodes processed
1662000 nodes processed
1662500 nodes processed
1663000 nodes processed
1663500 nodes processed
1664000 nodes processed
1664500 nodes processed
1665000 nodes processed
1665500 nodes processed
1666000 nodes processed
1666500 nodes processed
1667000 nodes processed
1667500 nodes processed
1668000 nodes processed
1668500 nodes processed
1669000 nodes processed
1669500 nodes processed
1670000 nodes processed
1670500 nodes processed
1671000 nodes processed
1671500 nodes processed
1672000 nodes processed
1672500 nodes processed
1673000 nodes processed
1673500 nodes processed
1674000 nodes processed
1674500 nodes processed
1675000 nodes processed
1675500 nodes processed
1676000 nodes processed
1676500 nodes processed
1677000 nodes processed
1677500 nodes processed
1678000 nodes processed
1678500 nodes processed
1679000 nodes processed
1679500 nodes processed
1680000 nodes processed
1680500 nodes processed
1681000 nodes processed
1681500 nodes pr

...

78609500 nodes processed
78610000 nodes processed
78610500 nodes processed
78611000 nodes processed
78611500 nodes processed
78612000 nodes processed
78612500 nodes processed
78613000 nodes processed
78613500 nodes processed
78614000 nodes processed
78614500 nodes processed
78615000 nodes processed
78615500 nodes processed
78616000 nodes processed
78616500 nodes processed
78617000 nodes processed
78617500 nodes processed
78618000 nodes processed
78618500 nodes processed
78619000 nodes processed
78619500 nodes processed
78620000 nodes processed
78620500 nodes processed
78621000 nodes processed
78621500 nodes processed
78622000 nodes processed
78622500 nodes processed
78623000 nodes processed
78623500 nodes processed
78624000 nodes processed
78624500 nodes processed
78625000 nodes processed
78625500 nodes processed
78626000 nodes processed
78626500 nodes processed
78627000 nodes processed
78627500 nodes processed
78628000 nodes processed
78628500 nodes processed
78629000 nodes processed


79020500 nodes processed
79021000 nodes processed
79021500 nodes processed
79022000 nodes processed
79022500 nodes processed
79023000 nodes processed
79023500 nodes processed
79024000 nodes processed
79024500 nodes processed
79025000 nodes processed
79025500 nodes processed
79026000 nodes processed
79026500 nodes processed
79027000 nodes processed
79027500 nodes processed
79028000 nodes processed
79028500 nodes processed
79029000 nodes processed
79029500 nodes processed
79030000 nodes processed
79030500 nodes processed
79031000 nodes processed
79031500 nodes processed
79032000 nodes processed
79032500 nodes processed
79033000 nodes processed
79033500 nodes processed
79034000 nodes processed
79034500 nodes processed
79035000 nodes processed
79035500 nodes processed
79036000 nodes processed
79036500 nodes processed
79037000 nodes processed
79037500 nodes processed
79038000 nodes processed
79038500 nodes processed
79039000 nodes processed
79039500 nodes processed
79040000 nodes processed


79387000 nodes processed
79387500 nodes processed
79388000 nodes processed
79388500 nodes processed
79389000 nodes processed
79389500 nodes processed
79390000 nodes processed
79390500 nodes processed
79391000 nodes processed
79391500 nodes processed
79392000 nodes processed
79392500 nodes processed
79393000 nodes processed
79393500 nodes processed
79394000 nodes processed
79394500 nodes processed
79395000 nodes processed
79395500 nodes processed
79396000 nodes processed
79396500 nodes processed
79397000 nodes processed
79397500 nodes processed
79398000 nodes processed
79398500 nodes processed
79399000 nodes processed
79399500 nodes processed
79400000 nodes processed
79400500 nodes processed
79401000 nodes processed
79401500 nodes processed
79402000 nodes processed
79402500 nodes processed
79403000 nodes processed
79403500 nodes processed
79404000 nodes processed
79404500 nodes processed
79405000 nodes processed
79405500 nodes processed
79406000 nodes processed
79406500 nodes processed


79828500 nodes processed
79829000 nodes processed
79829500 nodes processed
79830000 nodes processed
79830500 nodes processed
79831000 nodes processed
79831500 nodes processed
79832000 nodes processed
79832500 nodes processed
79833000 nodes processed
79833500 nodes processed
79834000 nodes processed
79834500 nodes processed
79835000 nodes processed
79835500 nodes processed
79836000 nodes processed
79836500 nodes processed
79837000 nodes processed
79837500 nodes processed
79838000 nodes processed
79838500 nodes processed
79839000 nodes processed
79839500 nodes processed
79840000 nodes processed
79840500 nodes processed
79841000 nodes processed
79841500 nodes processed
79842000 nodes processed
79842500 nodes processed
79843000 nodes processed
79843500 nodes processed
79844000 nodes processed
79844500 nodes processed
79845000 nodes processed
79845500 nodes processed
79846000 nodes processed
79846500 nodes processed
79847000 nodes processed
79847500 nodes processed
79848000 nodes processed


80215500 nodes processed
80216000 nodes processed
80216500 nodes processed
80217000 nodes processed
80217500 nodes processed
80218000 nodes processed
80218500 nodes processed
80219000 nodes processed
80219500 nodes processed
80220000 nodes processed
80220500 nodes processed
80221000 nodes processed
80221500 nodes processed
80222000 nodes processed
80222500 nodes processed
80223000 nodes processed
80223500 nodes processed
80224000 nodes processed
80224500 nodes processed
80225000 nodes processed
80225500 nodes processed
80226000 nodes processed
80226500 nodes processed
80227000 nodes processed
80227500 nodes processed
80228000 nodes processed
80228500 nodes processed
80229000 nodes processed
80229500 nodes processed
80230000 nodes processed
80230500 nodes processed
80231000 nodes processed
80231500 nodes processed
80232000 nodes processed
80232500 nodes processed
80233000 nodes processed
80233500 nodes processed
80234000 nodes processed
80234500 nodes processed
80235000 nodes processed


## concerting SWC files into 3D images

The SWC files can be rendered into volumetric JPEG images by Vaa3D plugins.